In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from datetime import datetime
import pmdarima as pm
from pmdarima.utils import diff
from sklearn.metrics import mean_squared_error
import pickle
import sklearn
import statsmodels.tsa.statespace as sm
from sklearn.preprocessing import StandardScaler

In [84]:
df = pd.read_csv('./../data/full_dataset_unscaled.csv')
df['zip'] = df['zip'].map(lambda x: str(x))
df['zip'] = df['zip'].map(lambda x: '0' + x if len(x)<5 else x)
df['datetime']=df['datetime'].map(lambda x: datetime.strptime(x, '%Y-%m-%d'))
df = df.set_index('datetime')

In [108]:
# from Mo/Niki

df['net_job_rate']=df['job_creation_rate']-df['job_destruction_rate']
df['apartment_for_rent_searches'] = df[['apartment for rent','studio for rent','1 bedroom for rent','3 bedroom for rent']].sum(axis=1)
df['multifamily_for_rent_searches'] = df[['townhome for rent','townhouse for rent','house for rent','duplex apartments for rent','condos for rent']].sum(axis=1)
df['gun_searches'] = df[['gun range', 'gun control', 'gun violence']].sum(axis=1)


acs_cols = ['percent_white',
 'percent_black',
 'percent_asian',
 'percent_hispanic',
 'percent_native_am',
 'percent_other_race',
 'percent_0_17',
 'percent_18_39',
 'percent_40_64',
 'percent_65+',
 'percent_rental_units_vacant',
 'percent_rental_units_occupied',
 'percent_graduate_deg',
 'percent_bachelors',
 'percent_associates',
 'percent_highschool',
 'percent_less_highschool',
 'percent_commute_public_transport',
 'percent_commute_less_30',
 'percent_buildings_less_10_units',
 'percent_buildings_10_19_units',
 'percent_buildings_20_49_units',
 'percent_buildings_50+_units',
 'percent_commute_30_to_59',
 'percent_commute_60_to_89',
 'percent_commute_90_more',
 'percent_new_city',
 'percent_new_unit',
 'percent_units_owner_occupied',
 'median_building_age',
 'income_per_capita',
 'poverty_rate',
 'total_pop',
 'percent_workforce_unemployed',
 'percent_work_from_home',
 'median_age',
 'percent_female',
 'gini_index',
 'percent_not_us_citizen']
acs_cols_remove=['percent_other_race','percent_40_64','percent_0_17','percent_18_39',
       'percent_65+','percent_rental_units_vacant','percent_not_us_citizen','percent_less_highschool', 'percent_buildings_less_10_units',
 'percent_commute_30_to_59',
 'percent_commute_60_to_89',
 'percent_commute_90_more', 'percent_commute_less_30','percent_graduate_deg',
                'percent_female','gini_index','percent_hispanic','percent_black','percent_bachelors',
                 'percent_asian','percent_new_city','percent_new_unit']
acs_cols_keep=list(set(acs_cols) - set(acs_cols_remove))
bikeshare_cols = ['bs_total_stations',
 'bs_total_systems',
 'has_bike_sharing']
bikeshare_cols_remove=['has_bike_sharing','bs_total_systems']
bikeshare_cols_keep=list(set(bikeshare_cols) - set(bikeshare_cols_remove))
trends_cols = ['gun range',
 'gun control',
 'gun violence',
 'job opportunities',
 'unemployment',
 'retirement',
 'layoff',
 'lgbt',
 'same sex marriage',
 'they',
 'pronouns',
 'black lives matter',
 'political correctness',
 'make america great again',
 'euthanasia',
 'getaway',
 'places to go',
 'flight tickets',
 'twitter',
 'hashtag',
 'fake news',
 'hurricane',
 'wildfire',
 'flood',
 'fire',
 "trader joe's",
 'whole foods',
 'lululemon',
 'thrift',
 'condos for rent',
 'duplex apartments for rent',
 'townhomes for rent',
 'townhouses for rent',
 'home for rent',
 'house for rent',
 'townhome for rent',
 'townhouse for rent',
 'apartment for rent',
 'studio for rent',
 '1 bedroom for rent',
 '3 bedroom for rent',
 'starbucks',
  'apartment_for_rent_searches',
  'multifamily_for_rent_searches',
  'gun_searches']
trends_cols_remove=['they','apartment for rent','studio for rent','1 bedroom for rent',
                    '3 bedroom for rent', 'townhome for rent','townhouse for rent',
                    'house for rent','duplex apartments for rent','condos for rent',
                   'gun range', 'gun control', 'gun violence']
trends_cols_keep=list(set(trends_cols) - set(trends_cols_remove))
economic_cols = ['total_firms',
 'job_creation_rate',
 'job_destruction_rate',
 'startup_firms','state_local_perc', 'net_job_rate']
economic_cols_remove=['total_firms', 'job_creation_rate','job_destruction_rate',]
economic_cols_keep=list(set(economic_cols) - set(economic_cols_remove))

In [86]:
df = df[df['year']>=2015]

In [87]:
def plot_arima(zip_code, pred_dict):
    fig = go.Figure()
    fig.add_trace(go.Line(x = y[y['zip']==zip_code].index, y = y[y['zip']==zip_code]['zri'], mode = 'lines'))
    fig.add_trace(go.Line(x = pred_dict[zip_code].index, y = pred_dict[zip_code], mode = 'lines'))
    fig.add_vline(x=y[y['zip']==zip_code].index[47], line_width=3, line_dash="dash", line_color="green")
    fig.show()

In [88]:
zips = list(df['zip'].unique())

y = df.drop(columns = ['year', 'month', 'City', 'State', 'Metro', 'CountyName']).loc[:,['zip', 'zri']]
x = df.drop(columns = ['year', 'month', 'City', 'State', 'Metro', 'CountyName', 'zri'])

In [89]:
actual_df = df[df['year']==2019].loc[:,['zip', 'zri']]

In [90]:
def calc_resids(pred_dict, actual_df):
    df = pd.DataFrame(pred_dict)
    df = df.iloc[47:,:].T.reset_index(drop=False).rename(columns = {'index':'zip'})
    df = df.melt(id_vars = 'zip', var_name = 'datetime', value_name = 'zri').sort_values(['zip', 'datetime'], ascending = True)
    df.set_index('datetime', inplace = True)
    resid_df = df.copy()
    resid_df['zri'] = resid_df['zri']-actual_df['zri']
    rmse = np.sqrt(((resid_df['zri']**2).sum().sum())/(1301*12))
    r2 = (df['zri'].corr(actual_df['zri']))**2
    return resid_df, rmse, r2

# ARIMA with no exogenous features

In [29]:
pred_dict_none = {}
coef_dict_none = {}

In [30]:
start = datetime.now()
for item in zips:
    curr_y = y[y['zip']==item]
    curr_y_train = curr_y.iloc[0:48,:]
    
    
    curr_model = sm.sarimax.SARIMAX(curr_y_train['zri'], exog = None, order = (1,1,0), seasonal_order=(0, 0, 0, 0)).fit()
    
    pred_dict_none[item] = curr_model.predict(start = 1, end = 59, exog = None, dynamic = 47)
    coef_dict_none[item] = curr_model.params

elapsed = datetime.now()-start
print(elapsed)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

...

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

0:02:00.424311


In [31]:
plot_arima('10128', pred_dict_none)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [32]:
resid_none, rmse_none, r2_none = calc_resids(pred_dict_none, actual_df)

In [33]:
print(rmse_none, r2_none)

62.99431968105214 0.9913744340000086


In [34]:
resid_none.to_csv('./arima_resids_no_exog.csv', index = True)

In [35]:
coef_none = pd.DataFrame(coef_dict_none)

In [36]:
coef_avg = pd.DataFrame(coef_none.sum(axis=1)/1301) # average coefficients

In [37]:
coef_std = np.std(coef_none.T)

In [38]:
coef_none = pd.concat([coef_avg, coef_std], axis = 1)

In [39]:
coef_none.columns = ['coef', 'std']

In [40]:
coef_none

coef         std
ar.L1     0.638740    0.134218
sigma2  152.105838  191.639971

In [41]:
coef_none.to_csv('./simple_arima_coefs.csv', index = True)

# Bikeshare data only

In [42]:
pred_dict_bike = {}
coef_dict_bike = {}

In [43]:
x_bike = x.loc[:,['zip']+bikeshare_cols_keep]

In [44]:
start = datetime.now()
for item in zips:
    curr_y = y[y['zip']==item]
    curr_x = x_bike[x_bike['zip']==item].drop(columns = 'zip')
    curr_y_train = curr_y.iloc[0:48,:]
    curr_x_train = curr_x.iloc[0:48,:]
    curr_x_test = curr_x.iloc[48:,:]
    
    curr_model = sm.sarimax.SARIMAX(curr_y_train['zri'], exog = curr_x_train, order = (1,1,0), seasonal_order=(0, 0, 0, 0)).fit()
    
    pred_dict_bike[item] = curr_model.predict(start = 1, end=59, exog = curr_x_test, dynamic = 47)
    coef_dict_bike[item] = curr_model.params

elapsed = datetime.now()-start
print(elapsed)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

...

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

0:02:56.745232


C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.



In [45]:
plot_arima('10128', pred_dict_bike)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [46]:
resid_bike, rmse_bike, r2_bike = calc_resids(pred_dict_bike, actual_df)

In [47]:
print(rmse_bike, r2_bike)

63.250793819355216 0.9913137786477039


In [48]:
resid_bike.to_csv('./sarimax_resids_bike.csv', index = True)

In [49]:
coef_bike = pd.DataFrame(coef_dict_bike)

In [50]:
coef_avg = pd.DataFrame(coef_bike.sum(axis=1)/1301) # average coefficients

In [51]:
coef_std = np.std(coef_bike.T)

In [52]:
coef_bike = pd.concat([coef_avg, coef_std], axis = 1)

In [53]:
coef_bike.columns = ['coef', 'std']

In [54]:
coef_bike

coef         std
bs_total_stations   -0.258437    3.457391
ar.L1                0.639757    0.133830
sigma2             150.780705  188.799689

In [55]:
coef_bike.to_csv('./sarimax_coef_bike.csv', index = True)

# ACS only

In [21]:
pred_dict_acs = {}
coef_dict_acs = {}

In [23]:
x_acs = x.loc[:,['zip']+acs_cols_keep]

In [25]:
start = datetime.now()
for item in zips:
    curr_y = y[y['zip']==item]
    curr_x = x_acs[x_acs['zip']==item].drop(columns = 'zip')
    curr_y_train = curr_y.iloc[0:48,:]
    curr_x_train = curr_x.iloc[0:48,:]
    curr_x_test = curr_x.iloc[48:,:]
    
    curr_model = sm.sarimax.SARIMAX(curr_y_train['zri'], exog = curr_x_train, order = (1,1,0), seasonal_order=(0, 0, 0, 0)).fit()
    
    pred_dict_acs[item] = curr_model.predict(start = 1, end = 59, exog = curr_x_test, dynamic = 47)
    coef_dict_acs[item] = curr_model.params

elapsed = datetime.now()-start
print(elapsed)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_mo

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_mo

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_mo

...

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_mo

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

0:14:29.520340


In [26]:
plot_arima('01013', pred_dict_acs)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [27]:
resid_acs, rmse_acs, r2_acs = calc_resids(pred_dict_acs, actual_df)
print(rmse_acs, r2_acs)
resid_acs.to_csv('./sarimax_resids_acs.csv', index = True)
coef_acs = pd.DataFrame(coef_dict_acs)
coef_avg = pd.DataFrame(coef_acs.sum(axis=1)/1301) # average coefficients
coef_std = np.std(coef_acs.T)
coef_acs = pd.concat([coef_avg, coef_std], axis = 1)
coef_acs.columns = ['coef', 'std']
coef_acs.sort_values('coef', ascending = False)

586.6061892489472 0.5413893885277506


coef         std
sigma2                            138.065331  175.872720
percent_workforce_unemployed       18.259584  226.639483
median_age                         17.799254  541.684186
poverty_rate                       14.387584  160.248653
median_building_age                 7.211916  338.007839
percent_buildings_50+_units         5.461560  132.455959
percent_buildings_20_49_units       2.352668  167.319773
percent_buildings_10_19_units       0.844195  152.055433
percent_work_from_home              0.752611  105.180483
ar.L1                               0.522458    0.179643
percent_native_am                   0.236085   18.526310
percent_units_owner_occupied        0.098408  216.939719
total_pop                           0.055334    0.946967
income_per_capita                   0.007550    0.526860
percent_associates                 -1.087829  231.077471
percent_highschool                 -1.330812  190.312869
percent_commute_public_transport   -6.360221  188.037956
percent_white                      -6.472918  177.438144
percent_rental_units_occupied      -6.925312  213.794442

In [28]:
coef_acs.to_csv('./sarimax_coef_acs.csv', index = True)

# Tax dataset

In [61]:
pred_dict_econ = {}
coef_dict_econ = {}

In [66]:
x_econ = x.loc[:,['zip']+economic_cols_keep].drop(columns = 'state_local_perc')

In [68]:
start = datetime.now()
for item in zips:
    curr_y = y[y['zip']==item]
    curr_x = x_econ[x_econ['zip']==item].drop(columns = 'zip')
    curr_y_train = curr_y.iloc[0:48,:]
    curr_x_train = curr_x.iloc[0:48,:]
    curr_x_test = curr_x.iloc[48:,:]
    
    curr_model = sm.sarimax.SARIMAX(curr_y_train['zri'], exog = curr_x_train, order = (1,1,0), seasonal_order=(0, 0, 0, 0)).fit()
    
    pred_dict_econ[item] = curr_model.predict(start = 1, end = 59, exog = curr_x_test, dynamic = 47)
    coef_dict_econ[item] = curr_model.params

elapsed = datetime.now()-start
print(elapsed)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

...

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\b

0:04:43.250452


In [69]:
plot_arima('10128', pred_dict_econ)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [70]:
resid_econ, rmse_econ, r2_econ = calc_resids(pred_dict_econ, actual_df)
print(rmse_econ, r2_econ)
resid_econ.to_csv('./sarimax_resids_econ.csv', index = True)
coef_econ = pd.DataFrame(coef_dict_econ)
coef_avg = pd.DataFrame(coef_econ.sum(axis=1)/1301) # average coefficients
coef_std = np.std(coef_econ.T)
coef_econ = pd.concat([coef_avg, coef_std], axis = 1)
coef_econ.columns = ['coef', 'std']
coef_econ.sort_values('coef', ascending = False)

63.901103829364885 0.9911623929017821


coef         std
sigma2         147.017522  187.329765
ar.L1            0.607520    0.152041
startup_firms    0.098110    1.593899
net_job_rate    -3.930558   80.008879

In [124]:
coef_econ.to_csv('./sarimax_coef_econ.csv', index = True)

# BDS dataset

In [ ]:
pred_dict_bds = {}
coef_dict_bds = {}

In [ ]:
x_bds = x.loc[:, ['zip']+bds_cols]

In [ ]:
start = datetime.now()
for item in zips:
    curr_y = y[y['zip']==item]
    curr_x = x_bds[x_bds['zip']==item].drop(columns = 'zip')
    curr_y_train = curr_y.iloc[0:48,:]
    curr_x_train = curr_x.iloc[0:48,:]
    curr_x_test = curr_x.iloc[48:,:]
    
    curr_model = sm.sarimax.SARIMAX(curr_y_train['zri'], exog = curr_x_train, order = (1,1,0), seasonal_order=(0, 0, 0, 0)).fit()
    
    pred_dict_bds[item] = curr_model.predict(start = 1, end=59, exog = curr_x_test, dynamic = 47)
    coef_dict_bds[item] = curr_model.params

elapsed = datetime.now()-start
print(elapsed)

In [ ]:
plot_arima('10128', pred_dict_bds)

In [ ]:
resid_bds, rmse_bds, r2_bds = calc_resids(pred_dict_bds, actual_df)
print(rmse_bds, r2_bds)
resid_bds.to_csv('./sarimax_resids_bds.csv', index = True)
coef_bds = pd.DataFrame(coef_dict_bds)
coef_avg = pd.DataFrame(coef_bds.sum(axis=1)/1301) # average coefficients
coef_std = np.std(coef_bds.T)
coef_bds = pd.concat([coef_avg, coef_std], axis = 1)
coef_bds.columns = ['coef', 'std']
coef_bds.sort_values('coef', ascending = False)

In [ ]:
coef_bds.to_csv('./sarimax_coef_bds.csv', index = True)

# Google trends

In [10]:
pred_dict_google = {}
coef_dict_google = {}

In [13]:
x_google = x.loc[:, ['zip']+trends_cols_keep]

In [15]:
start = datetime.now()
for item in zips:
    curr_y = y[y['zip']==item]
    curr_x = x_google[x_google['zip']==item].drop(columns = 'zip')
    curr_y_train = curr_y.iloc[0:48,:]
    curr_x_train = curr_x.iloc[0:48,:]
    curr_x_test = curr_x.iloc[48:,:]
    
    curr_model = sm.sarimax.SARIMAX(curr_y_train['zri'], exog = curr_x_train, order = (1,1,0), seasonal_order=(0, 0, 0, 0)).fit()
    
    pred_dict_google[item] = curr_model.predict(start = 1, end=59, exog = curr_x_test, dynamic = 47)
    coef_dict_google[item] = curr_model.params

elapsed = datetime.now()-start
print(elapsed)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\bas

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa

...

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa

0:33:51.538433


C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "


In [152]:
plot_arima('10128', pred_dict_google)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [17]:
resid_google, rmse_google, r2_google = calc_resids(pred_dict_google, actual_df)
print(rmse_google, r2_google)
resid_google.to_csv('./sarimax_resids_google.csv', index = True)
coef_google = pd.DataFrame(coef_dict_google)
coef_avg = pd.DataFrame(coef_google.sum(axis=1)/1301) # average coefficients
coef_std = np.std(coef_google.T)
coef_google = pd.concat([coef_avg, coef_std], axis = 1)
coef_google.columns = ['coef', 'std']
coef_google.sort_values('coef', ascending = False)

85.567272186862 0.9836588945899655


coef        std
sigma2                         45.485848  56.365265
trader joe's                    4.596704  16.192766
thrift                          3.233355  10.946341
places to go                    2.406336  11.880053
getaway                         2.389526   8.580480
pronouns                        1.682041   6.666740
townhouses for rent             0.922850   5.662502
ar.L1                           0.855191   0.079551
hashtag                         0.721106   6.772285
hurricane                       0.659808   4.032002
starbucks                       0.546082   9.927591
black lives matter              0.354641   3.344304
same sex marriage               0.250662   4.441855
layoff                          0.141529   5.191549
fake news                       0.085248   7.965212
multifamily_for_rent_searches   0.081680   2.591530
apartment_for_rent_searches     0.056665   3.102405
gun_searches                   -0.004294   2.102431
flight tickets                 -0.012760   5.542053
job opportunities              -0.086815   6.118678
whole foods                    -0.125316   8.538808
make america great again       -0.149826   5.900579
lgbt                           -0.204474   5.756635
fire                           -0.247878  17.021456
flood                          -0.524191   5.354932
lululemon                      -0.527285  14.195786
home for rent                  -0.548598   5.270907
political correctness          -0.612159   6.097620
wildfire                       -0.684691  14.500877
euthanasia                     -0.691706   4.012715
townhomes for rent             -1.115324   8.067118
twitter                        -1.355002  10.797074
retirement                     -2.617703  11.467960
unemployment                   -5.101720  12.823735

In [18]:
coef_google.to_csv('./sarimax_coef_google.csv', index = True)

# Google and ACS

In [ ]:
pred_dict_acsg = {}
coef_dict_acsg = {}

In [ ]:
x_acsg = x.drop(columns = (bikeshare_cols + tax_cols + bds_cols))

In [ ]:
start = datetime.now()
for item in zips:
    curr_y = y[y['zip']==item]
    curr_x = x_acsg[x_acsg['zip']==item].drop(columns = 'zip')
    curr_x_test = curr_x.iloc[48:,:]
    
    curr_model = sm.sarimax.SARIMAX(curr_y['zri'], exog = curr_x, order = (1,1,0), seasonal_order=(0, 0, 0, 0)).fit()
    
    pred_dict_acsg[item] = curr_model.predict(start = 1, exog = curr_x_test, dynamic = 47)
    coef_dict_acsg[item] = curr_model.params

elapsed = datetime.now()-start
print(elapsed)

In [ ]:
plot_arima('99654', pred_dict_acsg)

In [ ]:
resid_acsg, rmse_acsg, r2_acsg = calc_resids(pred_dict_acsg, actual_df)
print(rmse_acsg, r2_acsg)
resid_acsg.to_csv('./sarimax_resids_acsg.csv', index = True)
coef_acsg = pd.DataFrame(coef_dict_acsg)
coef_acsg = pd.DataFrame(coef_acsg.sum(axis=1)/1301) # average coefficients
print((rmse_none - rmse_acsg), (r2_acsg - r2_none))
coef_acsg.sort_values(0, ascending = False)

In [ ]:
coef_acsg.to_csv('./sarimax_coef_acsg.csv', index = True)

# Everything

In [131]:
pred_dict_all = {}
coef_dict_all = {}

In [132]:
x_all = x.loc[:, ['zip'] + acs_cols_keep + economic_cols_keep + trends_cols_keep + bikeshare_cols_keep]

In [134]:
start = datetime.now()
for item in zips:
    curr_y = y[y['zip']==item]
    curr_y_train = curr_y.iloc[0:48,:]
    curr_x = x_all[x_all['zip']==item].drop(columns = 'zip').drop(columns = 'state_local_perc')
    curr_x_train = curr_x.iloc[0:48,:]
    curr_x_test = curr_x.iloc[48:,:]
    
    curr_model = sm.sarimax.SARIMAX(curr_y_train['zri'], exog = curr_x_train, order = (1,1,0), seasonal_order=(0, 0, 0, 0)).fit()
    
    pred_dict_all[item] = curr_model.predict(start = 1, end = 59, exog = curr_x_test, dynamic = 47)
    coef_dict_all[item] = curr_model.params

elapsed = datetime.now()-start
print(elapsed)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:5

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524

...

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524: ValueWarning:

No frequency information was provided, so inferred frequency MS will be used.

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\tsa\base\tsa_model.py:524

0:16:33.710238


C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\statsmodels\base\model.py:566: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals



In [135]:
plot_arima('99654', pred_dict_all)

C:\Users\fayma\anaconda3\envs\env1\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [136]:
resid_all, rmse_all, r2_all = calc_resids(pred_dict_all, actual_df)
print(rmse_all, r2_all)
resid_all.to_csv('./sarimax_resids_all.csv', index = True)
coef_all = pd.DataFrame(coef_dict_all)
coef_all = pd.DataFrame(coef_all.sum(axis=1)/1301) # average coefficients
print((rmse_none - rmse_all), (r2_all - r2_none))
coef_all.sort_values(0, ascending = False)

19176.84799102373 0.009087398788932584
-19113.853671342677 -0.982287035211076


0
median_building_age               1399.429049
percent_workforce_unemployed       187.153949
percent_buildings_10_19_units      183.557008
median_age                         139.762877
sigma2                              40.540340
percent_highschool                  39.794558
percent_white                       31.290279
percent_units_owner_occupied        26.919578
bs_total_stations                    7.037463
trader joe's                         4.039484
thrift                               2.700701
getaway                              2.584774
pronouns                             0.819737
ar.L1                                0.630302
black lives matter                   0.600739
lgbt                                 0.585903
job opportunities                    0.534954
townhouses for rent                  0.527915
same sex marriage                    0.261379
fire                                 0.167311
places to go                         0.153113
multifamily_for_rent_searches        0.077137
twitter                              0.042866
apartment_for_rent_searches          0.027269
political correctness                0.015846
layoff                              -0.081763
gun_searches                        -0.094787
townhomes for rent                  -0.107897
make america great again            -0.231901
hurricane                           -0.325396
percent_buildings_50+_units         -0.407331
total_pop                           -0.410947
hashtag                             -0.424413
euthanasia                          -0.475478
flood                               -0.682240
income_per_capita                   -0.683623
startup_firms                       -0.722921
home for rent                       -0.888206
flight tickets                      -0.965692
fake news                           -0.983280
whole foods                         -1.192480
wildfire                            -1.371240
unemployment                        -1.486277
percent_native_am                   -1.595034
lululemon                           -2.555168
starbucks                           -2.662584
retirement                          -3.268572
percent_work_from_home              -9.531961
percent_associates                 -61.562700
percent_rental_units_occupied      -64.712881
percent_buildings_20_49_units     -131.066577
poverty_rate                      -147.000007
net_job_rate                      -158.251494
percent_commute_public_transport  -181.430816

In [140]:
coef_all[0] = coef_all[0].map(lambda x: abs(x))

In [151]:
coef_all[coef_all.index != 'sigma2'].sort_values(0, ascending = False)[0:14]/200

0
median_building_age               6.997145
percent_workforce_unemployed      0.935770
percent_buildings_10_19_units     0.917785
percent_commute_public_transport  0.907154
net_job_rate                      0.791257
poverty_rate                      0.735000
median_age                        0.698814
percent_buildings_20_49_units     0.655333
percent_rental_units_occupied     0.323564
percent_associates                0.307814
percent_highschool                0.198973
percent_white                     0.156451
percent_units_owner_occupied      0.134598
percent_work_from_home            0.047660

In [137]:
coef_all.to_csv('./sarimax_coef_all.csv', index = True)

In [144]:
px.bar()